$\newcommand\N{\mathbb N}
\newcommand\Z{\mathbb Z}
\newcommand\Q{\mathbb Q}
\newcommand\R{\mathbb R}
\newcommand\C{\mathbb C}
\newcommand\too\longrightarrow
\renewcommand\phi\varphi
\renewcommand\epsilon\varepsilon
\renewcommand\hat\widehat
\renewcommand\tilde\widetilde
\renewcommand\vec\overrightarrow
\renewcommand\bar\overline
\newcommand\fl[1]{\left\lfloor #1\right\rfloor}
\newcommand\llbracket{[\![}
\newcommand\rrbracket{]\!]}
\newcommand\bbr[2]{\llbracket #1,#2\rrbracket}
\newcommand\todo{{\bf TODO }}
\newcommand\prob{\mathbb P}
\newcommand\esp{\mathbb E}
\newcommand\var{\mathbb V}
\newcommand\tribu{\mathfrak T}$

# L'algorithme de Gram-Schmidt

Marc Lorenzi

7 juin 2025

In [ ]:
from fractions import Fraction
import random

## 1. Introduction

Soit $E$ un $\R$ espace vectoriel de dimension finie $n$ muni d'un produit scalaire $<\ ,\ >$. Donnons-nous une base $\mathcal B=(e_0,\ldots,e_{n-1})$ de $E$. Posons pour tout $k\in\bbr0{n-1}$,

$$u_k=e_k-\sum_{i=0}^{k-1}\frac{<e_k,u_i>}{<u_i,u_i>}u_i$$

La famille $\mathcal B'=(u_0,\ldots,u_{n-1})$ est alors une base orthogonale de $E$. De plus, pour tout $k\in\bbr0{n-1}$, ${\rm Vect}(u_0,\ldots,u_k)={\rm Vect}(e_0,\ldots,e_k)$.

**Remarque.** Pour $k=0$, la somme est vide et donc $u_0=e_0$. Ceci permet d'éviter d'avoir à « intialiser » notre définition par récurrence des $u_k$.

**Remarque.** Que se passe-t-il si on applique l'algorithme à une famille $\mathcal B$ qui n'est pas une base de $E$ ? Commme le cardinal de $\mathcal B$ est égal à la dimension de $E$, la famille $\mathcal B$ est liée. Soit $k$ le plus petit entier de $\bbr0{n-1}$ tel que $(e_0,\ldots,e_k)$ soit liée. On montre alors facilement que $e_k$ est combinaison linéaire de $e_0,\ldots, e_{k-1}$, donc aussi de $u_0,\ldots, u_{k-1}$. On obtient donc $u_k=0$.

Si $k<n-1$, alors une division par 0 se produit lorsqu'on calcule $u_{k+1}$, ce qui est évidemment fort ennuyeux.

Si $k=n-1$, alors la famille $(u_0,\ldots,u_{n-2})$ est une famille orthogonale de vecteurs non nuls. On n'effectue aucune division par 0 mais $u_{n-1}=0$, ce qui est tout aussi ennuyeux.

La fonction `gram_schmidt` prend en paramètres :

- la base $\mathcal B$, donnée par la liste des $e_i$.
- un paramètre $E$ qui est un quadruplet `(sub, prod, scal, nul)` où les fonctions `sub`, `prod`, `scal` et `nul` permettent le calcul de la différence de deux vecteurs de $E$, du produit d'un vecteur par un réel, du produit scalaire de deux vecteurs, et le test de la nullité d'un vecteur.

Elle renvoie la base orthogonale $\mathcal B'$.

In [ ]:
def gram_schmidt(B, E):
    sub, prod, scal, nul = E
    n = len(B)
    B1 = []
    for k in range(n):
        u = B[k]
        for i in range(k):
            t = scal(B[k], B1[i]) / scal(B1[i], B1[i])
            u = sub(u, prod(t, B1[i]))
        if nul(u): raise Exception('Famille liée')
        B1.append(u)
    return B1

Nous allons maintenant faire fonctionner l'algorithme sur deux exemples.

## 2. L'espace euclidien canonique $\R^n$

Munissons $\R^n$ du produit scalaire canonique

$$<x,y>=\sum_{i=0}^{n-1}x_iy_i$$

Nous représentons les vecteurs de $\R^n$ par des listes de réels de longueur $n$.

Définissons tout d'abord les fonctions `sub`, `prod`, `scal` et `nul`.

In [ ]:
def sub(u, v):
    n = len(u)
    return [u[k] - v[k] for k in range(n)]

In [ ]:
def prod(t, u):
    return [t * x for x in u]

In [ ]:
def scal(u, v):
    n = len(u)
    return sum([u[k] * v[k] for k in range(n)])

In [ ]:
def nul(u):
    n = len(u)
    return u == n * [0]

In [ ]:
Rn = (sub, prod, scal, nul)

Avant d'essayer `gram_schmidt`, écrivons quelques fonctions utilitaires.

La fonction `print_mat` affiche joliment une matrice de taille raisonnable.

In [ ]:
def print_mat(A):
    n = len(A)
    for i in range(n):
        for j in range(n):
            print('%10s' % A[i][j], end=' ')
        print()

La fonction `mat_scal` prend en paramètre une famille $\mathcal B=(e_0,\ldots,e_{n-1})$ de vecteurs en renvoie la matrice dont les coefficients sont les réels $A_{ij}=<e_i,e_j>$.

In [ ]:
def mat_scal(B, E):
    sub, prod, scal, nul = E
    n = len(B)
    return [[scal(B[i], B[j]) for j in range(n)] for i in range(n)]

Enfin, la fonction `rand_mat` renvoie une matrice carrée dont les coefficients sont des variables aléatoires suivant une loi uniforme sur $\{-1,0,1\}$. La matrice peut ne pas être inversible. Dans ce cas, Gram-Schmidt ne fonctionnera évidemment pas.

In [ ]:
def rand_mat(n):
    return [[Fraction(random.randint(-1,1)) for j in range(n)] for i in range(n)]

Voici une matrice « aléatoire » de taille 6 et la matrice des produits scalaires de ses lignes.

In [ ]:
B = rand_mat(6)
print_mat(B)
print()
print_mat(mat_scal(B, Rn))

Nous pouvons maintenant tester la fonction `gram_schmidt`.

Rappelons la remarque faite un peu plus haut concernant `rand_mat` : il est possible que `rand_mat` ait renvoyé une matrice non inversible ! Dans ce cas, l'évaluation de la cellule ci-dessous renvoie l'exception « Famille liée », ce qui est parfaitement normal.

In [ ]:
B = rand_mat(6)
print_mat(B)

In [ ]:
B1 = gram_schmidt(B, Rn)
print_mat(B1)

A-t-on bien une base orthogonale ? Facile à savoir, affichons la matrice des produits scalaires.

In [ ]:
print_mat(mat_scal(B1, Rn))

Nous obtenons une matrice diagonale. C'est ce qui était attendu.

## 3. La complexité de l'algorithme de Gram-Schmidt

Quelle est la complexité de notre fonction `gram_schmidt` ? Notons $C_{gs}(n)$ la complexité de la fonction `gram_schmidt` lorsqu'elle est appelée sur une base d'un espace euclidien de dimension $n$. De même, notons $C_{sub}(n)$, $C_{prod}(n)$, $C_{scal}(n)$ et $C_{nul}(n)$ les complexités des quatre fonctions définissant l'espace $E$. Le code de la fonction `gram_schmidt` nous donne

$$C_{gs}(n)=nC_{nul}(n)+(2C_{scal}(n)+C_{sub}(n)+C_{prod}(n))\sum_{k=0}^{n-1}k$$

Posons

$$C_E(n)=2C_{scal}(n)+C_{sub}(n)+C_{prod}(n)$$

On a donc

$$C_{gs}(n)=nC_{nul}(n)+\frac 1 2 n(n-1)C_E(n)$$

La valeur de $C_E(n)$ dépend évidemment de l'espace euclidien $E$ que nous considérons. Dans le cas de $\R^n$, nous avons $C_E(n)=C_{nul}(n)=O(n)$, et donc

$$C_{gs}(n)=O(n^3)$$

## 4. Polynômes

Munissons l'espace vectoriel $\R[X]$ des polynômes à coefficients réels du produit scalaire

$$<P<Q>=\int_{-1}^1P(x)Q(x)\,dx$$

L'algorithme de Gram-Schmidt appliqué à la base canonique $(X^n)_{n\in\N}$ renvoie les *polynômes de Legendre*.

Nous allons utiliser `sympy` pour opérer de façon exacte sur les polynômes. En particulier, le produit scalaire de deux polynômes est calculé par la fonction `integrate`, qui détermine la valeur exacte d'une intégrale. Soyons donc raisonnables sur le degré des polynômes que nous considérerons.

In [ ]:
from sympy import *

In [ ]:
X = Symbol('X')

In [ ]:
def sub1(P, Q): return P - Q 

In [ ]:
def prod1(t, P): return t * P

In [ ]:
def scal1(P, Q): return integrate(P * Q, (X, -1, 1))

In [ ]:
def nul1(P): return P == 0

In [ ]:
RX = (sub1, prod1, scal1, nul1)

Allons jusqu'au degré 6 ...

In [ ]:
B = [X ** k for k in range(7)]

In [ ]:
print_mat(mat_scal(B, RX))

Les valeurs sont celles attendues. En effet, pour tous $m,n\in\N$,

$$<X^m,X^n>=\int_{-1}^1x^{m+n}\,dx=\frac{1-(1)^{m+n+1}}{m+n+1}$$

In [ ]:
B1 = gram_schmidt(B, RX)

Voici les 7 premiers polynômes de Legendre.

In [ ]:
Matrix(B1).transpose()

In [ ]:
print_mat(mat_scal(B1, RX))

Ici encore, la matrice des produits scalaires est diagonale. La famille $\mathcal B_1$ est donc bien orthogonale.